In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [1]:
import numpy as np 
import pandas as pd 
import os
import re
import matplotlib.pyplot as plt
from tensorflow.python.keras.preprocessing.text import Tokenizer
from tensorflow.python.keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential
from keras.layers import Dense, Embedding, GRU, LSTM, Bidirectional
from keras.layers.embeddings import Embedding
from keras.initializers import Constant
from keras.callbacks import ModelCheckpoint
from keras.models import load_model

In [2]:
embeddings = {}
embedding_dim = 100

f = open("/content/drive/My Drive/glove.6B.100d.txt", encoding="utf-8")
for line in f:
    values = line.split()
    word = values[0]
    coefs = np.asarray(values[1:], dtype='float32')
    embeddings[word] = coefs
f.close()

print('Found %s word vectors.' % len(embeddings))

Found 400000 word vectors.


In [5]:
!unzip '/content/drive/My Drive/questions.csv.zip'

Archive:  /content/drive/My Drive/questions.csv.zip
  inflating: questions.csv           


In [3]:
def clean_text(text):
    
    
    pattern = re.compile('http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+]|[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+' )
    text = pattern.sub('', text)
    text = " ".join(filter(lambda x:x[0]!='@', text.split()))
    emoji = re.compile("["
                           u"\U0001F600-\U0001FFFF"  # emoticons
                           u"\U0001F300-\U0001F5FF"  # symbols & pictographs
                           u"\U0001F680-\U0001F6FF"  # transport & map symbols
                           u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
                           u"\U00002702-\U000027B0"
                           u"\U000024C2-\U0001F251"
                           "]+", flags=re.UNICODE)
    
    text = emoji.sub(r'', text)
    text = text.lower()
    text = re.sub(r"i'm", "i am", text)
    text = re.sub(r"he's", "he is", text)
    text = re.sub(r"she's", "she is", text)
    text = re.sub(r"that's", "that is", text)        
    text = re.sub(r"what's", "what is", text)
    text = re.sub(r"where's", "where is", text) 
    text = re.sub(r"\'ll", " will", text)  
    text = re.sub(r"\'ve", " have", text)  
    text = re.sub(r"\'re", " are", text)
    text = re.sub(r"\'d", " would", text)
    text = re.sub(r"\'ve", " have", text)
    text = re.sub(r"won't", "will not", text)
    text = re.sub(r"don't", "do not", text)
    text = re.sub(r"did't", "did not", text)
    text = re.sub(r"can't", "can not", text)
    text = re.sub(r"it's", "it is", text)
    text = re.sub(r"couldn't", "could not", text)
    text = re.sub(r"have't", "have not", text)
    text = re.sub(r"[,.\"\'!@#$%^&*(){}?/;`~:<>+=-]", "", text)
    return text

In [4]:
!pip install nltk


In [5]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [6]:
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [13]:
lines = data['question1'].values.tolist()

In [14]:
lines

['What is the step by step guide to invest in share market in india?',
 'What is the story of Kohinoor (Koh-i-Noor) Diamond?',
 'How can I increase the speed of my internet connection while using a VPN?',
 'Why am I mentally very lonely? How can I solve it?',
 'Which one dissolve in water quikly sugar, salt, methane and carbon di oxide?',
 'Astrology: I am a Capricorn Sun Cap moon and cap rising...what does that say about me?',
 'Should I buy tiago?',
 'How can I be a good geologist?',
 'When do you use シ instead of し?',
 'Motorola (company): Can I hack my Charter Motorolla DCX3400?',
 'Method to find separation of slits using fresnel biprism?',
 'How do I read and find my YouTube comments?',
 'What can make Physics easy to learn?',
 'What was your first sexual experience like?',
 'What are the laws to change your status from a student visa to a green card in the US, how do they compare to the immigration laws in Canada?',
 'What would a Trump presidency mean for current international 

In [9]:
from nltk.stem import PorterStemmer
from nltk.tokenize import TweetTokenizer

In [8]:
def process_tweet(tweet):
    """Process tweet function.
    Input:
        tweet: a string containing a tweet
    Output:
        tweets_clean: a list of words containing the processed tweet
    """
    tweet = str(tweet)
    stemmer = PorterStemmer()
    stopwords_english = stopwords.words('english')
    # remove stock market tickers like $GE
    tweet = re.sub(r'\$\w*', '', tweet)
    # remove old style retweet text "RT"
    tweet = re.sub(r'^RT[\s]+', '', tweet)
    # remove hyperlinks
    tweet = re.sub(r'https?:\/\/.*[\r\n]*', '', tweet)
    # remove hashtags
    # only removing the hash # sign from the word
    tweet = re.sub(r'#', '', tweet)
    # tokenize tweets
    tokenizer = TweetTokenizer(preserve_case=False, strip_handles=True,
                               reduce_len=True)
    tweet_tokens = tokenizer.tokenize(tweet)

    tweets_clean = []
    for word in tweet_tokens:
        if (word not in stopwords_english and  # remove stopwords
                word not in string.punctuation):  # remove punctuation
            # tweets_clean.append(word)
            stem_word = stemmer.stem(word)  # stemming word
            tweets_clean.append(stem_word)

    return tweets_clean

In [ ]:
lines = data['question1'].values.tolist()

In [60]:
ques = list()
que = list()

for tweet in lines:
    que = process_tweet(tweet)
    ques.append(que)
    

In [61]:
ques

[['step', 'step', 'guid', 'invest', 'share', 'market', 'india'],
 ['stori', 'kohinoor', 'koh-i-noor', 'diamond'],
 ['increas', 'speed', 'internet', 'connect', 'use', 'vpn'],
 ['mental', 'lone', 'solv'],
 ['one',
  'dissolv',
  'water',
  'quikli',
  'sugar',
  'salt',
  'methan',
  'carbon',
  'di',
  'oxid'],
 ['astrolog', 'capricorn', 'sun', 'cap', 'moon', 'cap', 'rise', '...', 'say'],
 ['buy', 'tiago'],
 ['good', 'geologist'],
 ['use', 'シ', 'instead', 'し'],
 ['motorola', 'compani', '):', 'hack', 'charter', 'motorolla', 'dcx', '3400'],
 ['method', 'find', 'separ', 'slit', 'use', 'fresnel', 'biprism'],
 ['read', 'find', 'youtub', 'comment'],
 ['make', 'physic', 'easi', 'learn'],
 ['first', 'sexual', 'experi', 'like'],
 ['law',
  'chang',
  'statu',
  'student',
  'visa',
  'green',
  'card',
  'us',
  'compar',
  'immigr',
  'law',
  'canada'],
 ['would',
  'trump',
  'presid',
  'mean',
  'current',
  'intern',
  'master',
  '’',
  'student',
  'f1',
  'visa'],
 ['manipul', 'mean'],


In [62]:
lines1 = data['question2'].values.tolist()

In [63]:
ques1 = list()
que1 = list()

for tweet in lines1:
    que1 = process_tweet(tweet)
    ques1.append(que1)
    

In [64]:
ques1

[['step', 'step', 'guid', 'invest', 'share', 'market'],
 ['would',
  'happen',
  'indian',
  'govern',
  'stole',
  'kohinoor',
  'koh-i-noor',
  'diamond',
  'back'],
 ['internet', 'speed', 'increas', 'hack', 'dn'],
 ['find', 'remaind', 'math', '23', '24', 'math', 'divid', '24,23'],
 ['fish', 'would', 'surviv', 'salt', 'water'],
 ["i'm", 'tripl', 'capricorn', 'sun', 'moon', 'ascend', 'capricorn', 'say'],
 ['keep', 'childern', 'activ', 'far', 'phone', 'video', 'game'],
 ['great', 'geologist'],
 ['use', 'instead'],
 ['hack', 'motorola', 'dcx', '3400', 'free', 'internet'],
 ['thing', 'technician', 'tell', 'durabl', 'reliabl', 'laptop', 'compon'],
 ['see', 'youtub', 'comment'],
 ['make', 'physic', 'easi', 'learn'],
 ['first', 'sexual', 'experi'],
 ['law',
  'chang',
  'statu',
  'student',
  'visa',
  'green',
  'card',
  'us',
  'compar',
  'immigr',
  'law',
  'japan'],
 ['trump',
  'presid',
  'affect',
  'student',
  'present',
  'us',
  'plan',
  'studi',
  'us'],
 ['manipul', 'mean'

In [47]:
# UNQ_C12 (UNIQUE CELL IDENTIFIER, DO NOT EDIT)
def get_document_embedding(tweet, en_embeddings): 
    '''
    Input:
        - tweet: a string
        - en_embeddings: a dictionary of word embeddings
    Output:
        - tweet_embedding: a
    '''
    doc_embedding = np.zeros(100)

    for word in tweet:
        # add the word embedding to the running total for the document embedding
        doc_embedding+=en_embeddings.get(word,0)
    ### END CODE HERE ###
    return doc_embedding

In [65]:
emb = get_document_embedding(ques[0], embeddings)

In [66]:
emb

array([ -0.03297402,   2.32462005,   1.65229801,   3.42622998,
         0.25195059,  -3.69062946,  -3.99909011,   0.23190598,
         0.43438001,  -0.15225295,  -0.74151   ,   0.28567705,
         0.632209  ,  -0.85055999,  -1.51423697,  -1.12979001,
        -0.84966003,   1.81608048,  -0.549057  ,   1.14564399,
         2.74055001,  -0.76897001,   0.11939993,   2.15176594,
        -1.15487696,   0.24783097,   1.40127002,   0.27787   ,
         0.134565  ,  -1.10666199,  -1.704587  ,   3.44028005,
        -1.23651097,  -1.68823802,   2.18523   ,   0.41771001,
         2.15896364,  -1.47815099,  -0.90826496,  -3.05641609,
        -1.73156001,  -0.84517002,   1.55854002,  -2.21905   ,
        -1.35500006,   0.88027   ,   0.52307093,   1.29941276,
        -1.06767999,  -6.07243899,  -1.34662394,  -0.40771298,
        -0.02055667,   6.1072199 ,  -2.20198798, -11.83615971,
        -2.70989398,  -0.75613979,  10.85005009,  -0.58741601,
        -0.093705  ,  -0.39367119,  -2.72031896,   1.12

In [67]:
emb1 = get_document_embedding(ques1[0], embeddings)

In [68]:
emb1

array([ 9.26695988e-01,  2.01667006e+00,  7.51777984e-01,  2.38983002e+00,
        2.48459995e-01, -2.88304947e+00, -2.86009005e+00, -5.79184011e-01,
        1.11294998e+00, -6.78342978e-01, -6.69257998e-01,  1.04180703e+00,
        1.03739016e-01, -1.94326000e+00, -9.95286988e-01, -9.16440010e-01,
       -1.03150003e+00,  1.41570050e+00,  1.05642982e-01,  7.99383976e-01,
        1.81807002e+00, -5.18959999e-01, -1.05850003e+00,  1.54170596e+00,
       -1.18463996e+00, -1.89969018e-01,  8.64800021e-01, -4.10399973e-01,
       -1.12550035e-02, -8.32201999e-01, -1.20169701e+00,  2.40368006e+00,
       -9.38000981e-01, -1.35896801e+00,  1.93579000e+00,  7.55500019e-01,
        2.15064004e+00, -1.26442098e+00, -4.49284971e-01, -2.82200608e+00,
       -4.35760036e-01, -1.59316003e+00,  7.76620008e-01, -1.46261002e+00,
       -2.19875006e+00,  1.39752000e+00, -5.72129011e-01,  7.81732775e-01,
       -1.34674000e+00, -6.03891999e+00, -1.18932395e+00, -1.14731299e+00,
       -4.18306657e-01,  

In [69]:
cosine_similarity(emb, emb1)

0.9761450074987604

In [70]:
embss=[]
embsss=[]
for b in ques:
  embss = get_document_embedding(b, embeddings)
  embsss.append(embss)

In [71]:
embsss

[array([ -0.03297402,   2.32462005,   1.65229801,   3.42622998,
          0.25195059,  -3.69062946,  -3.99909011,   0.23190598,
          0.43438001,  -0.15225295,  -0.74151   ,   0.28567705,
          0.632209  ,  -0.85055999,  -1.51423697,  -1.12979001,
         -0.84966003,   1.81608048,  -0.549057  ,   1.14564399,
          2.74055001,  -0.76897001,   0.11939993,   2.15176594,
         -1.15487696,   0.24783097,   1.40127002,   0.27787   ,
          0.134565  ,  -1.10666199,  -1.704587  ,   3.44028005,
         -1.23651097,  -1.68823802,   2.18523   ,   0.41771001,
          2.15896364,  -1.47815099,  -0.90826496,  -3.05641609,
         -1.73156001,  -0.84517002,   1.55854002,  -2.21905   ,
         -1.35500006,   0.88027   ,   0.52307093,   1.29941276,
         -1.06767999,  -6.07243899,  -1.34662394,  -0.40771298,
         -0.02055667,   6.1072199 ,  -2.20198798, -11.83615971,
         -2.70989398,  -0.75613979,  10.85005009,  -0.58741601,
         -0.093705  ,  -0.39367119,  -2.

In [72]:
embss1=[]
embsss1=[]
for b in ques1:
  embss1 = get_document_embedding(b, embeddings)
  embsss1.append(embss1)

In [73]:
embsss1

[array([ 9.26695988e-01,  2.01667006e+00,  7.51777984e-01,  2.38983002e+00,
         2.48459995e-01, -2.88304947e+00, -2.86009005e+00, -5.79184011e-01,
         1.11294998e+00, -6.78342978e-01, -6.69257998e-01,  1.04180703e+00,
         1.03739016e-01, -1.94326000e+00, -9.95286988e-01, -9.16440010e-01,
        -1.03150003e+00,  1.41570050e+00,  1.05642982e-01,  7.99383976e-01,
         1.81807002e+00, -5.18959999e-01, -1.05850003e+00,  1.54170596e+00,
        -1.18463996e+00, -1.89969018e-01,  8.64800021e-01, -4.10399973e-01,
        -1.12550035e-02, -8.32201999e-01, -1.20169701e+00,  2.40368006e+00,
        -9.38000981e-01, -1.35896801e+00,  1.93579000e+00,  7.55500019e-01,
         2.15064004e+00, -1.26442098e+00, -4.49284971e-01, -2.82200608e+00,
        -4.35760036e-01, -1.59316003e+00,  7.76620008e-01, -1.46261002e+00,
        -2.19875006e+00,  1.39752000e+00, -5.72129011e-01,  7.81732775e-01,
        -1.34674000e+00, -6.03891999e+00, -1.18932395e+00, -1.14731299e+00,
        -4.1

In [74]:
len(embsss)

404351

In [75]:
len(embsss1)

404351

In [76]:
sim=[]
simi=[]

for i in range(len(embsss1)):
  simi = cosine_similarity(embsss[i], embsss1[i])
  sim.append(simi)
  

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:17: RuntimeWarning: invalid value encountered in double_scalars


In [77]:
sim

[0.9761450074987604,
 0.3069249629335496,
 0.8171119402760222,
 0.37213636639978537,
 0.8982296462770881,
 0.7638206777993042,
 0.34789080343613604,
 0.8744734469644553,
 1.0000000000000002,
 0.763796053622894,
 0.5465004784005684,
 0.9103767574132392,
 0.9999999999999999,
 0.941464064194777,
 0.9860482068913782,
 0.8332928660664987,
 0.9999999999999999,
 0.9612130712008274,
 0.8492867395304344,
 0.9349487461704965,
 0.8841273083409743,
 -0.2990024173784095,
 1.0,
 0.5525070922293859,
 0.8827443380439767,
 1.0000000000000002,
 0.8235101995508796,
 0.7312026242925536,
 0.9788483881421857,
 0.8886027249066883,
 0.9753399482410298,
 0.9363821881179752,
 0.9872604432959816,
 0.3358495313687773,
 0.9009429412307163,
 0.8774670169731664,
 0.8650121920555168,
 0.9234927940049257,
 0.14167629148476607,
 0.8691551712193191,
 0.3592807898877713,
 1.0,
 0.9974891867839502,
 0.823340958259009,
 0.8846563549096726,
 0.7676615603363134,
 -0.22067728097250452,
 0.729503531567158,
 0.9864478759568649,

In [85]:
for i in range(len(sim)):
  if sim[i] >= 0.5:
    sim[i] = 1
  if sim[i] < 0.5:
    sim[i] = 0
  else:
    sim[i] = sim[i]

In [97]:
for i in range(len(sim)):
  if sim[i] >= 0.5:
    sim[i] = 1
  else:
    sim[i] = 0

In [98]:
sim

[1,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 0,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 0,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,


In [99]:
def isnan(value):
  try:
      import math
      return math.isnan(float(value))
  except:
      return False

In [100]:
isnan(sim[0])

False

In [101]:
for i in range(len(sim)):
  if isnan(sim[i])==True:
    print(i)
  

In [102]:
len(sim)

404351

In [103]:
len(data['is_duplicate'])

404351

In [104]:
from sklearn.metrics import accuracy_score
accuracy_score(data['is_duplicate'], sim)

0.43865354605281054

In [41]:

# UNQ_C1 (UNIQUE CELL IDENTIFIER, DO NOT EDIT)
def cosine_similarity(A, B):
    '''
    Input:
        A: a numpy array which corresponds to a word vector
        B: A numpy array which corresponds to a word vector
    Output:
        cos: numerical number representing the cosine similarity between A and B.
    '''

    ### START CODE HERE (REPLACE INSTANCES OF 'None' with your code) ###
    
    dot = np.dot(A,B)
    norma = np.sqrt(np.dot(A,A))
    normb = np.sqrt(np.dot(B,B))
    cos = dot / (norma*normb)

    ### END CODE HERE ###
    return cos

In [11]:
data = pd.read_csv('questions.csv')

In [12]:
data

id  ...  is_duplicate
0            0  ...             0
1            1  ...             0
2            2  ...             0
3            3  ...             0
4            4  ...             0
...        ...  ...           ...
404346  404346  ...             0
404347  404347  ...             1
404348  404348  ...             0
404349  404349  ...             0
404350  404350  ...             0

[404351 rows x 6 columns]

In [48]:
data['question1'].head(100)

0     What is the step by step guide to invest in sh...
1     What is the story of Kohinoor (Koh-i-Noor) Dia...
2     How can I increase the speed of my internet co...
3     Why am I mentally very lonely? How can I solve...
4     Which one dissolve in water quikly sugar, salt...
                            ...                        
95                           How does 3D printing work?
96    What was it like to attend Caltech with Jeremy...
97                      Why did harry become a horcrux?
98    What are the best associate product manager (A...
99    Why is the number for Skype at 1-855-425-3768 ...
Name: question1, Length: 100, dtype: object

In [16]:
lines = data['question2'].values.tolist()

In [17]:
lines

['What is the step by step guide to invest in share market?',
 'What would happen if the Indian government stole the Kohinoor (Koh-i-Noor) diamond back?',
 'How can Internet speed be increased by hacking through DNS?',
 'Find the remainder when [math]23^{24}[/math] is divided by 24,23?',
 'Which fish would survive in salt water?',
 "I'm a triple Capricorn (Sun, Moon and ascendant in Capricorn) What does this say about me?",
 'What keeps childern active and far from phone and video games?',
 'What should I do to be a great geologist?',
 'When do you use "&" instead of "and"?',
 'How do I hack Motorola DCX3400 for free internet?',
 'What are some of the things technicians can tell about the durability and reliability of Laptops and its components?',
 'How can I see all my Youtube comments?',
 'How can you make physics easy to learn?',
 'What was your first sexual experience?',
 'What are the laws to change your status from a student visa to a green card in the US? How do they compare to 